In [10]:
import os 

import matplotlib as mpl
from matplotlib import pyplot as plt
import numpy as np

from tqdm import notebook
import torch
from torch.utils.data import DataLoader
from torch.nn import functional as F
from torchvision import transforms
import torchvision
from torchvision import models, io
import plotly.express as px
from plotly import graph_objects as go
from ipywidgets import widgets, interact

mpl.rcParams["figure.figsize"] = (10, 10)

In [11]:
%load_ext autoreload

%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [12]:
from face_landmarks import LandMarkDatset, SquarePaddingResize, denormalize_landmarks

In [13]:
def plot_landmarks(image_info):
    image = image_info["image"].permute(1, 2, 0)
    height, width = image.shape[:2]
    landmarks = image_info["landmarks"] 
    plt.imshow(image)
    plt.plot(landmarks[:, 0], landmarks[:, 1], "g+", markersize=1)

In [17]:
dir_path = os.path.join("data", "test-train", "contest01_data")

In [18]:
data = LandMarkDatset(path_to_dir=dir_path, is_train=True, transformations=None)

ValueError: Index file_name invalid

In [ ]:
plot_landmarks(data[123])

In [8]:
del data

In [9]:
import pickle

In [10]:
with open(os.path.join("data", "features", "train_emb.pickle"), "rb") as file:
    features = pickle.load(file)

In [11]:
features.shape

(64000, 1024)

In [12]:
dataset = LandMarkDatset(dir_path, is_train=True, transformations=None)

In [133]:
from sklearn import ensemble, cluster, svm, neighbors

In [136]:
# outlier_detection = ensemble.IsolationForest(n_estimators=100, n_jobs=-1, verbose=True)
outlier_detection = cluster.DBSCAN(n_jobs=-1)

In [137]:
predictions = outlier_detection.fit_predict(features)

In [139]:
(predictions == -1).shape

(64000,)

In [124]:
images = dataset.index2img_name(np.argwhere(predictions == -1).reshape(-1))

In [125]:
image_dir = os.path.join(dir_path, "train", "images")

In [126]:
tensor_images = []
for image_name in images:
    image_tensor = io.read_image(os.path.join(image_dir, image_name))
    image_tensor = transforms.Resize((197, 256))(image_tensor)
    tensor_images.append(image_tensor)

In [127]:
def show_image(image_index, tensor_images):
    figure = go.FigureWidget()
    figure.add_trace(go.Image(z=tensor_images[image_index].permute(1, 2, 0)))
    return figure

In [128]:
list_widget = widgets.Dropdown(options=tuple(range(len(images))))

In [129]:
interact(show_image, image_index=list_widget, tensor_images=widgets.fixed(tensor_images))

interactive(children=(Dropdown(description='image_index', options=(0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 1…

<function __main__.show_image(image_index, tensor_images)>

In [101]:
import umap

In [114]:
umap_embder = umap.UMAP(n_components=2, n_neighbors=100, metric="cosine")

In [115]:
emb = umap_embder.fit_transform(features)

In [116]:
img_names = dataset.index2img_name(tuple(range(features.shape[0])))

In [130]:
fig = go.Figure(data=go.Scattergl(x=emb[:, 0], y=emb[:, 1], mode='markers', marker_color=predictions, hovertext=img_names))
fig.show()